In [4]:
import pandas as pd
import numpy as np
import os, sys
import math
import copy

## PROCESS FIRST SAMPLE

In [89]:
# I NEED TO DUPLICATE BACKSLASHES AT THE VERY END OF THE STRINGS OR IT FAILS
input = [r'.|...\....',
r'|.-.\.....',
r'.....|-...',
r'........|.',
r'..........',
'.........\\',
r'..../.\\..',
r'.-.-/..|..',
'.|....-|.\\',
r'..//.|....']

In [90]:
beam_movement = {'>':[0,1], '<':[0,-1],'^':[-1,0],'v':[1,0]}

beam_transform = {'>': {'.':['>'], '|':['^','v'], '-':['>'],'\\':['v'],'/':['^']},
                   '<': {'.':['<'], '|':['^','v'], '-':['<'],'\\':['^'],'/':['v']}, 
                   '^': {'.':['^'], '|':['^'], '-':['<','>'],'\\':['<'],'/':['>']}, 
                   'v': {'.':['v'], '|':['v'], '-':['<','>'],'\\':['>'],'/':['<']}}

In [91]:
map = []
for line in input:
    line_items = [x for x in line]
    map.append(line_items)
np_map = np.array(map)
print(map)
print(np_map.shape)
print(np_map)

[['.', '|', '.', '.', '.', '\\', '.', '.', '.', '.'], ['|', '.', '-', '.', '\\', '.', '.', '.', '.', '.'], ['.', '.', '.', '.', '.', '|', '-', '.', '.', '.'], ['.', '.', '.', '.', '.', '.', '.', '.', '|', '.'], ['.', '.', '.', '.', '.', '.', '.', '.', '.', '.'], ['.', '.', '.', '.', '.', '.', '.', '.', '.', '\\'], ['.', '.', '.', '.', '/', '.', '\\', '\\', '.', '.'], ['.', '-', '.', '-', '/', '.', '.', '|', '.', '.'], ['.', '|', '.', '.', '.', '.', '-', '|', '.', '\\'], ['.', '.', '/', '/', '.', '|', '.', '.', '.', '.']]
(10, 10)
[['.' '|' '.' '.' '.' '\\' '.' '.' '.' '.']
 ['|' '.' '-' '.' '\\' '.' '.' '.' '.' '.']
 ['.' '.' '.' '.' '.' '|' '-' '.' '.' '.']
 ['.' '.' '.' '.' '.' '.' '.' '.' '|' '.']
 ['.' '.' '.' '.' '.' '.' '.' '.' '.' '.']
 ['.' '.' '.' '.' '.' '.' '.' '.' '.' '\\']
 ['.' '.' '.' '.' '/' '.' '\\' '\\' '.' '.']
 ['.' '-' '.' '-' '/' '.' '.' '|' '.' '.']
 ['.' '|' '.' '.' '.' '.' '-' '|' '.' '\\']
 ['.' '.' '/' '/' '.' '|' '.' '.' '.' '.']]


In [106]:
def energize_map(beams,np_map):

    beam_map = {}
    while len(beams) > 0:
        this_beam = beams.pop(0)
        this_position = this_beam['position']
        position_idx = tuple(this_position)
        this_type = this_beam['type']
        if position_idx in beam_map.keys():
            if this_type in beam_map[position_idx]:         # THIS BEAM IN THIS POSITION HAS ALREADY BEEN COVERED, SKIP BEAM
                continue
            else:
                beam_map[position_idx].append(this_type)    # OTHERWISE ADD THE BEAM TO THE LIST OF BEAMS COVERED IN THIS POSITION
        else:
            beam_map[position_idx] = [this_type]            # IF IT'S A NEW POSITION, INAUGURATE THE LIST OF BEAMS COVERED WITH THE CURRENT BEAM

        next_position = np.add(this_position , beam_movement[this_type])
        if np.min(next_position)<0:                         # NEGATIVE OUT OF BOUNDS IS NOT CATCHED BY INDEXERROR
            continue
        try:
            next_terrain = np_map[next_position[0], next_position[1]]
        except IndexError: # OUT OF MAP: DISAPPEAR
            continue
        next_beam_types = beam_transform[this_beam['type']][next_terrain]
        for next_beam_type in next_beam_types:
            beams.append({'type':next_beam_type, 'position': next_position})


    energized = 0
    for row in range(np_map.shape[0]):
        rowchars = []
        for col in range(np_map.shape[1]):
            if (row,col) in beam_map.keys():
                rowchars.append('#')
                energized += 1
            else:
                rowchars.append('.')
        print(''.join(rowchars))
    print(energized)
    return energized

In [93]:
beams = [{'type':'>', 'position':[0,-1]}]

energize_map(beams, np_map)

######....
.#...#....
.#...#####
.#...##...
.#...##...
.#...##...
.#..####..
########..
.#######..
.#...#.#..
46


## PROCESS PART 1

In [94]:
# READ FILE
inputfilepath = './input.txt'

input = []
with open(inputfilepath,'r') as f:
    for line in f:
        input.append(line.rstrip())

In [95]:
map = []
for line in input:
    line_items = [x for x in line]
    map.append(line_items)
np_map = np.array(map)
print(map)
print(np_map.shape)
print(np_map)

[['\\', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '-', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '|', '.', '.', '\\', '.', '.', '-', '.', '.', '.', '.', '-', '.', '.', '.', '.', '.', '.', '-', '.', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '|', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '-', '.', '\\', '.', '.', '.', '.', '.', '.', '|', '.', '.'], ['.', '.', '.', '.', '.', '.', '-', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '-', '.', '.', '.', '.', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '|', '.', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '.', '-'

In [96]:
beams = [{'type':'>', 'position':[0,-1]}]

energize_map(beams, np_map)

#.#......##...........##.......################################......#..#......###.......#....................
#.#......##.......#######################.#.......#.#..###...##......#..#......###.......#....................
##############################.#..#.##....#.......#.#..###...##......#..#......###.......#....................
..#......##########################.##....#.......#.#..###...##......#..#......###.......#...#################
..#......##.......##..########.#....##....#.......#.#..###...##......#..#......###.......#...#................
..#......##.......##..#.....##.#....##....#.......#.#..###..##########..#......###.......#...#................
..#......##.....################....##....#.......#.#..###..###......#..#......###.......#...#................
..#......##.....#.##..#....##########################..###..###......#..#......###.......#...#................
..#......##.....#.###############...##....#.......###..###..###......#..#......###.......#...#................
.

## PROCESS SECOND SAMPLE

In [99]:
# I NEED TO DUPLICATE BACKSLASHES AT THE VERY END OF THE STRINGS OR IT FAILS
input = [r'.|...\....',
r'|.-.\.....',
r'.....|-...',
r'........|.',
r'..........',
'.........\\',
r'..../.\\..',
r'.-.-/..|..',
'.|....-|.\\',
r'..//.|....']

In [100]:
map = []
for line in input:
    line_items = [x for x in line]
    map.append(line_items)
np_map = np.array(map)
print(map)
print(np_map.shape)
print(np_map)

[['.', '|', '.', '.', '.', '\\', '.', '.', '.', '.'], ['|', '.', '-', '.', '\\', '.', '.', '.', '.', '.'], ['.', '.', '.', '.', '.', '|', '-', '.', '.', '.'], ['.', '.', '.', '.', '.', '.', '.', '.', '|', '.'], ['.', '.', '.', '.', '.', '.', '.', '.', '.', '.'], ['.', '.', '.', '.', '.', '.', '.', '.', '.', '\\'], ['.', '.', '.', '.', '/', '.', '\\', '\\', '.', '.'], ['.', '-', '.', '-', '/', '.', '.', '|', '.', '.'], ['.', '|', '.', '.', '.', '.', '-', '|', '.', '\\'], ['.', '.', '/', '/', '.', '|', '.', '.', '.', '.']]
(10, 10)
[['.' '|' '.' '.' '.' '\\' '.' '.' '.' '.']
 ['|' '.' '-' '.' '\\' '.' '.' '.' '.' '.']
 ['.' '.' '.' '.' '.' '|' '-' '.' '.' '.']
 ['.' '.' '.' '.' '.' '.' '.' '.' '|' '.']
 ['.' '.' '.' '.' '.' '.' '.' '.' '.' '.']
 ['.' '.' '.' '.' '.' '.' '.' '.' '.' '\\']
 ['.' '.' '.' '.' '/' '.' '\\' '\\' '.' '.']
 ['.' '-' '.' '-' '/' '.' '.' '|' '.' '.']
 ['.' '|' '.' '.' '.' '.' '-' '|' '.' '\\']
 ['.' '.' '/' '/' '.' '|' '.' '.' '.' '.']]


In [101]:
starting_beams = {'>':{'row':[x for x in range(np_map.shape[0])], 'col':[-1]},'<':{'row':[x for x in range(np_map.shape[0])], 'col':[np_map.shape[1]]},'^':{'col':[x for x in range(np_map.shape[1])], 'row':[np_map.shape[0]]},'v':{'col':[x for x in range(np_map.shape[1])], 'row':[-1]}}
starting_beams

{'>': {'row': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9], 'col': [-1]},
 '<': {'row': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9], 'col': [10]},
 '^': {'col': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9], 'row': [10]},
 'v': {'col': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9], 'row': [-1]}}

In [107]:
# CHECK ALL STARTING POINTS
max_energy = 0
for beam_type, ranges in starting_beams.items():
    for starting_row in ranges['row']:
        for starting_col in ranges['col']:
            print(f'{beam_type} {starting_row} {starting_col}')
            beams = [{'type':beam_type, 'position':[starting_row,starting_col]}]
            max_energy = max(max_energy, energize_map(beams, np_map))
max_energy

> 0 -1
######....
.#...#....
.#...#####
.#...##...
.#...##...
.#...##...
.#..####..
########..
.#######..
.#...#.#..
46
> 1 -1
#.........
#.........
#.........
#.........
#.........
#.........
#.........
#.........
#.........
#.........
10
> 2 -1
.#####....
.#...#....
##########
.#...##...
.#...##...
.#...##...
.#..####..
########..
.#######..
.#...#.#..
49
> 3 -1
........#.
........#.
........#.
#########.
........#.
........#.
........#.
........#.
........#.
........#.
18
> 4 -1
..........
..........
..........
..........
##########
..........
..........
..........
..........
..........
10
> 5 -1
..........
..........
..........
..........
..........
##########
.........#
.........#
.........#
..........
13
> 6 -1
#.........
#####.....
#...#.....
#...#.....
#...#.....
#...#.....
#####.....
#.........
#.........
#.........
22
> 7 -1
.#####....
.#...#....
.#...#####
.#...##...
.#...##...
.#...##...
.#..####..
########..
.#######..
.#...#.#..
45
> 8 -1
.#####....
.#...#....
.#...#####


51

## PROCESS PART 2

In [108]:
# READ FILE
inputfilepath = './input.txt'

input = []
with open(inputfilepath,'r') as f:
    for line in f:
        input.append(line.rstrip())

In [109]:
map = []
for line in input:
    line_items = [x for x in line]
    map.append(line_items)
np_map = np.array(map)
print(map)
print(np_map.shape)
print(np_map)

[['\\', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '-', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '|', '.', '.', '\\', '.', '.', '-', '.', '.', '.', '.', '-', '.', '.', '.', '.', '.', '.', '-', '.', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '|', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '-', '.', '\\', '.', '.', '.', '.', '.', '.', '|', '.', '.'], ['.', '.', '.', '.', '.', '.', '-', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '-', '.', '.', '.', '.', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '.', '|', '.', '.', '.', '.', '.', '/', '.', '.', '.', '.', '.', '.', '.', '.', '.', '-'

In [110]:
starting_beams = {'>':{'row':[x for x in range(np_map.shape[0])], 'col':[-1]},'<':{'row':[x for x in range(np_map.shape[0])], 'col':[np_map.shape[1]]},'^':{'col':[x for x in range(np_map.shape[1])], 'row':[np_map.shape[0]]},'v':{'col':[x for x in range(np_map.shape[1])], 'row':[-1]}}
starting_beams

{'>': {'row': [0,
   1,
   2,
   3,
   4,
   5,
   6,
   7,
   8,
   9,
   10,
   11,
   12,
   13,
   14,
   15,
   16,
   17,
   18,
   19,
   20,
   21,
   22,
   23,
   24,
   25,
   26,
   27,
   28,
   29,
   30,
   31,
   32,
   33,
   34,
   35,
   36,
   37,
   38,
   39,
   40,
   41,
   42,
   43,
   44,
   45,
   46,
   47,
   48,
   49,
   50,
   51,
   52,
   53,
   54,
   55,
   56,
   57,
   58,
   59,
   60,
   61,
   62,
   63,
   64,
   65,
   66,
   67,
   68,
   69,
   70,
   71,
   72,
   73,
   74,
   75,
   76,
   77,
   78,
   79,
   80,
   81,
   82,
   83,
   84,
   85,
   86,
   87,
   88,
   89,
   90,
   91,
   92,
   93,
   94,
   95,
   96,
   97,
   98,
   99,
   100,
   101,
   102,
   103,
   104,
   105,
   106,
   107,
   108,
   109],
  'col': [-1]},
 '<': {'row': [0,
   1,
   2,
   3,
   4,
   5,
   6,
   7,
   8,
   9,
   10,
   11,
   12,
   13,
   14,
   15,
   16,
   17,
   18,
   19,
   20,
   21,
   22,
   23,
   24,
   25,
   26,
   27,
   

In [111]:
# CHECK ALL STARTING POINTS
max_energy = 0
for beam_type, ranges in starting_beams.items():
    for starting_row in ranges['row']:
        for starting_col in ranges['col']:
            print(f'{beam_type} {starting_row} {starting_col}')
            beams = [{'type':beam_type, 'position':[starting_row,starting_col]}]
            max_energy = max(max_energy, energize_map(beams, np_map))
max_energy

> 0 -1
#.#......##...........##.......################################......#..#......###.......#....................
#.#......##.......#######################.#.......#.#..###...##......#..#......###.......#....................
##############################.#..#.##....#.......#.#..###...##......#..#......###.......#....................
..#......##########################.##....#.......#.#..###...##......#..#......###.......#...#################
..#......##.......##..########.#....##....#.......#.#..###...##......#..#......###.......#...#................
..#......##.......##..#.....##.#....##....#.......#.#..###..##########..#......###.......#...#................
..#......##.....################....##....#.......#.#..###..###......#..#......###.......#...#................
..#......##.....#.##..#....##########################..###..###......#..#......###.......#...#................
..#......##.....#.###############...##....#.......###..###..###......#..#......###.......#...#...........

8221